![Logo 1](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech1.jpg)
<div class="alert alert-block alert-info">
<h1> Modelowanie języka</h1>
<h2> 09. <i>Zanurzenia słów (Word2vec)</i>  [wykład]</h2> 
<h3> Filip Graliński (2022)</h3>
</div>

![Logo 2](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech2.jpg)



## Zanurzenia słów (Word2vec)



W praktyce stosowalność słowosieci okazała się zaskakująco
ograniczona. Większy przełom w przetwarzaniu języka naturalnego przyniosły
wielowymiarowe reprezentacje słów, inaczej: zanurzenia słów.



### „Wymiary” słów



Moglibyśmy zanurzyć (ang. *embed*) w wielowymiarowej przestrzeni, tzn. zdefiniować odwzorowanie
$E \colon V \rightarrow \mathcal{R}^m$ dla pewnego $m$ i określić taki sposób estymowania
prawdopodobieństw $P(u|v)$, by dla par $E(v)$ i $E(v')$ oraz $E(u)$ i $E(u')$ znajdujących się w pobliżu
(według jakiejś metryki odległości, na przykład zwykłej odległości euklidesowej):

$$P(u|v) \approx P(u'|v').$$

$E(u)$ nazywamy zanurzeniem (embeddingiem) słowa.



#### Wymiary określone z góry?



Można by sobie wyobrazić, że $m$ wymiarów mogłoby być z góry
określonych przez lingwistę. Wymiary te byłyby związane z typowymi
„osiami” rozpatrywanymi w językoznawstwie, na przykład:

-   czy słowo jest wulgarne, pospolite, potoczne, neutralne czy książkowe?
-   czy słowo jest archaiczne, wychodzące z użycia czy jest neologizmem?
-   czy słowo dotyczy kobiet, czy mężczyzn (w sensie rodzaju gramatycznego i/lub
    socjolingwistycznym)?
-   czy słowo jest w liczbie pojedynczej czy mnogiej?
-   czy słowo jest rzeczownikiem czy czasownikiem?
-   czy słowo jest rdzennym słowem czy zapożyczeniem?
-   czy słowo jest nazwą czy słowem pospolitym?
-   czy słowo opisuje konkretną rzecz czy pojęcie abstrakcyjne?
-   …

W praktyce okazało się jednak, że lepiej, żeby komputer uczył się sam
możliwych wymiarów — z góry określamy tylko $m$ (liczbę wymiarów).



### Bigramowy model języka oparty na zanurzeniach



Zbudujemy teraz najprostszy model język oparty na zanurzeniach. Będzie to właściwie najprostszy
**neuronowy model języka**, jako że zbudowany model można traktować jako prostą sieć neuronową.



#### Słownik



W typowym neuronowym modelu języka rozmiar słownika musi być z góry
ograniczony. Zazwyczaj jest to liczba rzędu kilkudziesięciu wyrazów —
po prostu będziemy rozpatrywać $|V|$ najczęstszych wyrazów, pozostałe zamienimy
na specjalny token `<unk>` reprezentujący nieznany (*unknown*) wyraz.

Aby utworzyć taki słownik, użyjemy gotowej klasy `Vocab` z pakietu torchtext:



In [8]:
from itertools import islice
import regex as re
import sys
from torchtext.vocab import build_vocab_from_iterator
import lzma

def get_words_from_line(line):
  line = line.rstrip()
  yield '<s>'
  for m in re.finditer(r'[\p{L}0-9\*]+|\p{P}+', line):
     yield m.group(0).lower()
  yield '</s>'


def get_word_lines_from_file(file_name):
  counter=0
  with lzma.open(file_name, 'r') as fh:
    for line in fh:
      counter+=1
      if counter == 100000:
        break
      line = line.decode("utf-8")
      yield get_words_from_line(line)

vocab_size = 20000

vocab = build_vocab_from_iterator(
    get_word_lines_from_file('train/in.tsv.xz'),
    max_tokens = vocab_size,
    specials = ['<unk>'])

vocab['jest']

12531

In [9]:
import pickle
with open("vocab.pickle", 'wb') as handle:
    pickle.dump(vocab, handle)

In [11]:
with open("vocab.pickle", 'rb') as handle:
    vocab = pickle.load( handle)

In [16]:
vocab['love']

838

In [ ]:
vocab.lookup_token()

In [4]:
!pip3 install torchtext

Please see https://github.com/pypa/pip/issues/5599 for advice on fixing the underlying issue.
To avoid this problem you can invoke Python with '-m pip' instead of running pip directly.
Defaulting to user installation because normal site-packages is not writeable
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.0/2.0 MB 661.8 kB/s eta 0:00:0000:0100:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.6/4.6 MB 1.1 MB/s eta 0:00:0000:0100:010m
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 619.9/619.9 MB 2.7 MB/s eta 0:00:0000:0100:02
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 177.1/177.1 MB 6.4 MB/s eta 0:00:0000:0100:01
  Using cached nvidia_cuda_runtime_cu11-11.7.99-py3-none-manylinux1_x86_64.whl (849 kB)
  Using cached nvidia_cuda_nvrtc_cu11-11.7.99-2-py3-none-manylinux1_x86_64.whl (21.0 MB)
  Using cached nvidia_cudnn_cu11-8.5.0.96-2-py3-none-manylinux1_x86_64.whl (557.1 MB)
  Using cached nvidia_cublas_cu11-11.10.3.66-py3-none-manylinux1_x86_64.whl (317.1 MB)
     ━━━━━━━━━━━━━━━━━━━━

In [17]:
vocab.lookup_tokens([0, 1, 2, 10, 12345])

['<unk>', '\\', 'the', '-\\', 'wno']

#### Definicja sieci



Naszą prostą sieć neuronową zaimplementujemy używając frameworku PyTorch.



In [18]:
def look_ahead_iterator(gen):
    prev = None
    for item in gen:
        if prev is not None:
            yield (prev, item)
        prev = item

In [23]:
list(look_ahead_iterator([1,2,3,4,5, 'X', 6 ]))

[(1, 2), (2, 3), (3, 4), (4, 5), (5, 'X'), ('X', 6)]

In [24]:
import itertools

In [34]:
from torch import nn
import torch

embed_size = 100

class SimpleBigramNeuralLanguageModel(nn.Module):
  def __init__(self, vocabulary_size, embedding_size):
      super(SimpleBigramNeuralLanguageModel, self).__init__()
      self.model = nn.Sequential(
          nn.Embedding(vocabulary_size, embedding_size),
          nn.Linear(embedding_size, vocabulary_size),
          nn.Softmax()
      )

  def forward(self, x):
      return self.model(x)

model = SimpleBigramNeuralLanguageModel(vocab_size, embed_size)

vocab.set_default_index(vocab['<unk>'])
ixs = torch.tensor(vocab.forward(['pies']))
# out[0][vocab['jest']]

Teraz wyuczmy model. Wpierw tylko potasujmy nasz plik:

    shuf < opensubtitlesA.pl.txt > opensubtitlesA.pl.shuf.txt



In [25]:
from torch.utils.data import IterableDataset
import itertools

def look_ahead_iterator(gen):
   prev = None
   for item in gen:
      if prev is not None:
         yield (prev, item)
      prev = item

class Bigrams(IterableDataset):
  def __init__(self, text_file, vocabulary_size):
      self.vocab = build_vocab_from_iterator(
         get_word_lines_from_file(text_file),
         max_tokens = vocabulary_size,
         specials = ['<unk>'])
      self.vocab.set_default_index(self.vocab['<unk>'])
      self.vocabulary_size = vocabulary_size
      self.text_file = text_file

  def __iter__(self):
     return look_ahead_iterator(
         (self.vocab[t] for t in itertools.chain.from_iterable(get_word_lines_from_file(self.text_file))))

train_dataset = Bigrams('train/in.tsv.xz', vocab_size)

In [32]:
from torch.utils.data import DataLoader

next(iter(train_dataset))

TypeError: 'tuple' object is not an iterator

In [29]:
vocab.lookup_tokens([43, 0])

['<s>', '<unk>']

In [1]:
from torch.utils.data import DataLoader

next(iter(DataLoader(train_dataset, batch_size=5)))

[tensor([   2,    5,   51, 3481,  231]), tensor([   5,   51, 3481,  231,    4])]

In [35]:
device = 'cpu'
model = SimpleBigramNeuralLanguageModel(vocab_size, embed_size).to(device)
data = DataLoader(train_dataset, batch_size=5000)
optimizer = torch.optim.Adam(model.parameters())
criterion = torch.nn.NLLLoss()

model.train()
step = 0
for x, y in data:
   x = x.to(device)
   y = y.to(device)
   optimizer.zero_grad()
   ypredicted = model(x)
   loss = criterion(torch.log(ypredicted), y)
   if step % 100 == 0:
      print(step, loss)
   step += 1
   loss.backward()
   optimizer.step()

torch.save(model.state_dict(), 'model1.bin')

/home/mikolaj/.local/lib/python3.8/site-packages/torch/nn/modules/container.py:217: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  input = module(input)


0 tensor(10.0877, grad_fn=<NllLossBackward0>)


/home/mikolaj/.local/lib/python3.8/site-packages/torch/autograd/__init__.py:200: UserWarning: CUDA initialization: The NVIDIA driver on your system is too old (found version 10020). Please update your GPU driver by downloading and installing a new version from the URL: http://www.nvidia.com/Download/index.aspx Alternatively, go to: https://pytorch.org to install a PyTorch version that has been compiled with your version of the CUDA driver. (Triggered internally at ../c10/cuda/CUDAFunctions.cpp:109.)
  Variable._execution_engine.run_backward(  # Calls into the C++ engine to run the backward pass


100 tensor(8.4388, grad_fn=<NllLossBackward0>)
200 tensor(7.7335, grad_fn=<NllLossBackward0>)
300 tensor(7.1300, grad_fn=<NllLossBackward0>)
400 tensor(6.7325, grad_fn=<NllLossBackward0>)
500 tensor(6.4705, grad_fn=<NllLossBackward0>)
600 tensor(6.0460, grad_fn=<NllLossBackward0>)
700 tensor(5.8104, grad_fn=<NllLossBackward0>)
800 tensor(5.8110, grad_fn=<NllLossBackward0>)
900 tensor(5.7169, grad_fn=<NllLossBackward0>)
1000 tensor(5.7580, grad_fn=<NllLossBackward0>)
1100 tensor(5.6787, grad_fn=<NllLossBackward0>)
1200 tensor(5.4501, grad_fn=<NllLossBackward0>)


KeyboardInterrupt: 

In [36]:
torch.save(model.state_dict(), 'model1.bin')

Policzmy najbardziej prawdopodobne kontynuacje dla zadanego słowa:



In [37]:
device = 'cpu'
model = SimpleBigramNeuralLanguageModel(vocab_size, embed_size).to(device)
model.load_state_dict(torch.load('model1.bin'))
model.eval()

ixs = torch.tensor(vocab.forward(['dla'])).to(device)

out = model(ixs)
top = torch.topk(out[0], 10)
top_indices = top.indices.tolist()
top_probs = top.values.tolist()
top_words = vocab.lookup_tokens(top_indices)
list(zip(top_words, top_indices, top_probs))

[(',', 3, 0.12514805793762207),
 ('\\', 1, 0.07237359136343002),
 ('<unk>', 0, 0.06839419901371002),
 ('.', 4, 0.06109621003270149),
 ('of', 5, 0.04557998105883598),
 ('and', 6, 0.03565318509936333),
 ('the', 2, 0.029342489317059517),
 ('to', 7, 0.02185475267469883),
 ('-\\', 10, 0.018097609281539917),
 ('in', 9, 0.016023961827158928)]

Teraz zbadajmy najbardziej podobne zanurzenia dla zadanego słowa:



In [38]:
vocab = train_dataset.vocab
ixs = torch.tensor(vocab.forward(['kłopot'])).to(device)

out = model(ixs)
top = torch.topk(out[0], 10)
top_indices = top.indices.tolist()
top_probs = top.values.tolist()
top_words = vocab.lookup_tokens(top_indices)
list(zip(top_words, top_indices, top_probs))

[(',', 3, 0.12514805793762207),
 ('\\', 1, 0.07237359136343002),
 ('<unk>', 0, 0.06839419901371002),
 ('.', 4, 0.06109621003270149),
 ('of', 5, 0.04557998105883598),
 ('and', 6, 0.03565318509936333),
 ('the', 2, 0.029342489317059517),
 ('to', 7, 0.02185475267469883),
 ('-\\', 10, 0.018097609281539917),
 ('in', 9, 0.016023961827158928)]

In [39]:
cos = nn.CosineSimilarity(dim=1, eps=1e-6)

embeddings = model.model[0].weight

vec = embeddings[vocab['poszedł']]

similarities = cos(vec, embeddings)

top = torch.topk(similarities, 10)

top_indices = top.indices.tolist()
top_probs = top.values.tolist()
top_words = vocab.lookup_tokens(top_indices)
list(zip(top_words, top_indices, top_probs))

[('<unk>', 0, 1.0000001192092896),
 ('nb', 1958, 0.4407886266708374),
 ('refrain', 14092, 0.4395471513271332),
 ('cat', 3391, 0.4154242277145386),
 ('enjoying', 7521, 0.3915165066719055),
 ('active', 1383, 0.38935279846191406),
 ('stewart', 4816, 0.3806381821632385),
 ('omit', 15600, 0.380504310131073),
 ('2041095573313', 11912, 0.37909239530563354),
 ('shut', 3863, 0.3778260052204132)]

#### Zapis przy użyciu wzoru matematycznego



Powyżej zaprogramowaną sieć neuronową można opisać następującym wzorem:

$$\vec{y} = \operatorname{softmax}(CE(w_{i-1}),$$

gdzie:

-   $w_{i-1}$ to pierwszy wyraz w bigramie (poprzedzający wyraz),
-   $E(w)$ to zanurzenie (embedding) wyrazy $w$ — wektor o rozmiarze $m$,
-   $C$ to macierz o rozmiarze $|V| \times m$, która rzutuje wektor zanurzenia w wektor o rozmiarze słownika,
-   $\vec{y}$ to wyjściowy wektor prawdopodobieństw o rozmiarze $|V|$.



##### Hiperparametry



Zauważmy, że nasz model ma dwa hiperparametry:

-   $m$ — rozmiar zanurzenia,
-   $|V|$ — rozmiar słownika, jeśli zakładamy, że możemy sterować
    rozmiarem słownika (np. przez obcinanie słownika do zadanej liczby
    najczęstszych wyrazów i zamiany pozostałych na specjalny token, powiedzmy, `<UNK>`.

Oczywiście możemy próbować manipulować wartościami $m$ i $|V|$ w celu
polepszenia wyników naszego modelu.

**Pytanie**: dlaczego nie ma sensu wartość $m \approx |V|$ ? dlaczego nie ma sensu wartość $m = 1$?



#### Diagram sieci



Jako że mnożenie przez macierz ($C$) oznacza po prostu zastosowanie
warstwy liniowej, naszą sieć możemy interpretować jako jednowarstwową
sieć neuronową, co można zilustrować za pomocą następującego diagramu:

![img](./09_Zanurzenia_slow/bigram1.drawio.png "Diagram prostego bigramowego neuronowego modelu języka")



#### Zanurzenie jako mnożenie przez macierz



Uzyskanie zanurzenia ($E(w)$) zazwyczaj realizowane jest na zasadzie
odpytania (<sub>look</sub>-up\_). Co ciekawe, zanurzenie można intepretować jako
mnożenie przez macierz zanurzeń (embeddingów) $E$ o rozmiarze $m \times |V|$ — jeśli słowo będziemy na wejściu kodowali przy użyciu
wektora z gorącą jedynką (<sub>one</sub>-hot encoding\_), tzn. słowo $w$ zostanie
podane na wejściu jako wektor $\vec{1_V}(w) = [0,\ldots,0,1,0\ldots,0]$ o rozmiarze $|V|$
złożony z samych zer z wyjątkiem jedynki na pozycji odpowiadającej indeksowi wyrazu $w$ w słowniku $V$.

Wówczas wzór przyjmie postać:

$$\vec{y} = \operatorname{softmax}(CE\vec{1_V}(w_{i-1})),$$

gdzie $E$ będzie tym razem macierzą $m \times |V|$.

**Pytanie**: czy $\vec{1_V}(w)$ intepretujemy jako wektor wierszowy czy kolumnowy?

W postaci diagramu można tę interpretację zilustrować w następujący sposób:

![img](./09_Zanurzenia_slow/bigram2.drawio.png "Diagram prostego bigramowego neuronowego modelu języka z wejściem w postaci one-hot")

